In [854]:
import random

In [855]:
events = True
verbose = False
tiempos = False

#### Parámetros

In [856]:
# Ejemplo del enunciado
T = 30*24*60 # 24h en minutos
# T = 100 #un mes en minutos #pongo 1 dia

nPistas = 3
nCoches = 20
nPuertas = 50

# lambda0 = getlambda0(t)
mu11 = 10.007615178514001
sigma11 = 3.0377002745229005
a12 = 10
b12 = 15
lambda2 = 1 / 2
lambda3 = 0.1

# T, nCoches, nPuertas, mu11, sigma11, a12, b12, lambda2, lambda3

In [857]:
def getlambda0(t):
    # t está en minutos, convertir a horas:
    t = t/60
    t = t%24 ##########ojo esto##########
    # Intervalo de 0 a 5 horas, lineal de 5 a 7
    if 0 <= t < 5:
        return 5 + (7 - 5) * (t - 0) / (5 - 0)
    # Intervalo de 5 a 8 horas, lineal de 7 a 6
    elif 5 <= t < 8:
        return 7 + (6 - 7) * (t - 5) / (8 - 5)
    # Intervalo de 8 a 15 horas, lineal de 6 a 9
    elif 8 <= t < 15:
        return 6 + (9 - 6) * (t - 8) / (15 - 8)
    # Intervalo de 15 a 17 horas, lineal de 9 a 6
    elif 15 <= t < 17:
        return 9 + (6 - 9) * (t - 15) / (17 - 15)
    # Intervalo de 17 a 24 horas, lineal de 6 a 5
    elif 14 <= t <= 24:
        return 6 + (5 - 6) * (t - 17) / (24 - 17)
    # Si el tiempo está fuera del rango de 0 a 24 horas
    else:
        return 10E9  

#### Funciones auxiliares para generación de tiempos

In [858]:
# Funciones auxiliares generacion de tiempos
def t_llegada(t):
    return random.expovariate(getlambda0(t))*60 #nº muy pequeños, tiene sentido?

def t_aterrizaje():
    # return np.random.normal(mu11, sigma11)
    # return random.normalvariate(mu11, sigma11) 
    while True:  # Bucle infinito hasta obtener un número válido
        resultado = random.normalvariate(mu11, sigma11)
        if resultado > 0:  # Comprobar si el resultado es mayor que cero
            return resultado
        
def t_traslado(): #N1- N2
    return random.expovariate(1/lambda2)

def t_desembarques():
    return random.expovariate(1/lambda3)

def t_salidas():
    return random.uniform(a12, b12)

#### Variables

In [859]:
def reiniciar_variables():
    global t, n1, n2, n3, NLL1, LL1, LISTA, LANDING, S3, DEPARTURE, acumulo_pistas_ocupadas, cambio_pistas_ocupadas
    global n_med_n1, n_med_n2, n_med_n3
    global esperando_a_despegar, esperando_a_aterrizar, esperando_coche, esperando_puerta
    
    t = 0                   # Variable reloj. tiempo asíncrono.
    n1 = n2 = n3 = 0        # Variables de estado nº clientes
    NLL1 = NLL2 = NLL3 = 0  # Variables contador nº llegadas
    NS1 = NS2 = NS3 = 0     # Variables contador nº salidas

    # Lista de tiempos de eventos
    LISTA = {
        'tLL1': 10E9,   
        'tS1':  [10E9]*nPistas,
        'tS2':  [10E9]*nCoches,
        'tS3':  [10E9]*nPuertas,
        'tSS':  [10E9]*nPistas
    }

    # Arrays for arrival and departure times
    LL1 = [] # tiempo de llegada de aviones
    LL2 = []
    LL3 = []
    S1 = []
    S2 = []
    S3 = [] # tiempo de llegada a la pista para despegar

    #Landing and departure times
    LANDING = []
    DEPARTURE = []

    # Colas
    esperando_a_despegar = 0
    esperando_a_aterrizar = 0
    esperando_coche = 0
    esperando_puerta = 0

    n_med_n1 = n_med_n2 = n_med_n3 = 0 # nº medio de aviones en el aeropuerto

    acumulo_pistas_ocupadas = cambio_pistas_ocupadas = 0



#### Rutina de aterrizaje

In [860]:

def rutina_aterrizaje(t_suc):
    
    global t, n1, n2, n3, NLL1, LL1, LISTA, LANDING, S3, DEPARTURE, acumulo_pistas_ocupadas, cambio_pistas_ocupadas
    global n_med_n1, n_med_n2, n_med_n3
    global esperando_a_despegar, esperando_a_aterrizar, esperando_coche, esperando_puerta
    
    # para luego calcular numero medio de clientes
    n_med_n1 += n1 * (t_suc - t) #tiempo trascurrido hasta el suceso * nº aviones
    n_med_n2 += n2 * (t_suc - t)
    n_med_n3 += n3 * (t_suc - t)
    
    LL1.append(t_suc) #anoto tiempo de llegada
    # Si tengo pista libre, aterrizo
    if (n1 < nPistas):
        # Actualizo variables contadores
        n1 += 1                     # El avión entra en n1, y ocupa una pista.
        if verbose: print(f'#### {n1} aviones en el nodo 1 ###')
        NLL1 += 1                   # numero de llegadas al n1
        if cambio_pistas_ocupadas > 0:
            acumulo_pistas_ocupadas += t_suc - cambio_pistas_ocupadas
            if tiempos: print(f'PISTA LIBRE AT {t_suc}. Acumulo {t_suc - cambio_pistas_ocupadas} -> {acumulo_pistas_ocupadas}')
            cambio_pistas_ocupadas = 0
            
        # LL1.append(t_suc)
        t = t_suc
        Z = t_aterrizaje() #random.normalvariate(mu11, sigma11) #genero tiempo aterrizaje
        LISTA['tS1'][LISTA['tS1'].index(10E9)] = t + Z
        
        LANDING.append(t) #anoto el tiempo en el que comienza el aterrizaje
        
        if events: print(f'ATERRIZAJE: {n1} pistas ocupadas. Minuto: {t}. Fin de maniobra: {t+Z}')
    
    # si no tengo pista, no aterrizo, me pongo en cola aterrizaje
    else:
        esperando_a_aterrizar+=1
        #si ya estaban ocupadas de antes, no actualices y quédate con el primero
        if cambio_pistas_ocupadas > 0 and t_suc > 0: 
            cambio_pistas_ocupadas = min(t_suc, cambio_pistas_ocupadas)
            if tiempos: print(f'Pista ocupada despegue en (t_suc, cambio) {t_suc, cambio_pistas_ocupadas} pero lo estaba antes en {cambio_pistas_ocupadas}')
        #si no lo estaban, actualiza el tiempo
        cambio_pistas_ocupadas = t_suc
        if tiempos: print(f'NO HAY PISTAS LIBRES at {cambio_pistas_ocupadas}')
        if events: print(f'ESPERANDO ATERRIZAR: {esperando_a_aterrizar} aviones esperando. Minuto {t}')
    #=========================================================================#

    # Genero tiempo siguente llegada
    Y = t_llegada(t)
    # Compruebo si el siguiente avión llega antes de T
    if (t + Y < T):
        LISTA['tLL1'] = t + Y #añado otro tiempo de llegada
        # print(f'NUEVO AVIÓN: Minuto: {t+Y}')
    else:
        if events: print(f'#### HORIZONTE ALCANZADO: {t+Y} > {T}, no llegan más aviones ####')
        if verbose: print(f'#### n1 = {n1}, n2 = {n2}, n3 = {n3} ####')
        if verbose: print(LISTA)


#### Rutina de traslado

In [861]:
def rutina_traslado(t_suc): 
    # un coche recoge al avión y lo desaloja de la pista (salida de N1)
    global t, n1, n2, n3, NLL1, LL1, LISTA, LANDING, S3, DEPARTURE, acumulo_pistas_ocupadas, cambio_pistas_ocupadas
    global n_med_n1, n_med_n2, n_med_n3
    global esperando_a_despegar, esperando_a_aterrizar, esperando_coche, esperando_puerta
    
    n_med_n1 += n1 * (t_suc - t) #tiempo trascurrido hasta el suceso * nº aviones
    n_med_n2 += n2 * (t_suc - t)
    n_med_n3 += n3 * (t_suc - t)
    
    t=t_suc     # Actualizamos tº de simulación
    n1 -=1      # El avión sale del nodo 1, y despeja una pista
    if cambio_pistas_ocupadas > 0:
        acumulo_pistas_ocupadas += t_suc - cambio_pistas_ocupadas
        if tiempos: print(f'PISTA LIBRE AT {t_suc}. Acumulo {t_suc - cambio_pistas_ocupadas} -> {acumulo_pistas_ocupadas}')
        cambio_pistas_ocupadas = 0
    # si hay coches disponibles -> traslado
    if n2 < nCoches:
        
        n2 +=1                  # El avion entra en n2, y ocupa un coche
        # tiempo de salida del N2, que se corresponde con el final del traslado
        Z = t_traslado()
        LISTA['tS2'][LISTA['tS2'].index(10E9)] = t + Z 

        if events: print(f'-TRASLADO: {n2} coches ocupados. Minuto {t}. Fin de traslado {t+Z}')
        
    else: #si no hay coche disponibles 
        esperando_coche +=1 #lo pongo a la cola de ser trasladado
        if events: print('-ESPERANDO COCHE: {esperando_coche} aviones esperando. Minuto {t}')

    if esperando_a_aterrizar > 0: # ahora que se han liberado pistas, atendemos a la cola de aterrizaje
        Z = t_aterrizaje()                              # genero tiempo que tardará en aterrizar
        LISTA['tS1'][LISTA['tS1'].index(10E9)] = t + Z  # registro el tiempo en el que saldrá el avión del nodo 1
        LANDING.append(t)
        n1+=1                       # El avión en cola entra al n1, ocupa una pista,
        esperando_a_aterrizar -= 1  # y libera su puesto en la cola.
        if events: print(f'ATERRIZAJE_cola: {n1} pistas ocupadas. Minuto: {t}. Fin de maniobra: {t+Z}')
        
    elif esperando_a_despegar > 0:

        if esperando_a_aterrizar>0: return -1
        
        n1+=1                       # El avión en cola entra al n1, ocupa una pista,
        esperando_a_despegar -=1    # Y libera su puesto en la cola.
        DEPARTURE.append(t)         # Registro tiempo en el que empieza a despegar
        Z = t_salidas()                                 # genero tiempo que tardará en despegar
        LISTA['tSS'][LISTA['tSS'].index(10E9)] = t + Z  # registro el tiempo en el que saldrá el avión del nodo 1

        
        if events: print(f'---DESPEGUE_cola: {n1} pistas ocupadas. Minuto: {t}. Fin de maniobra: {t+Z}')
        

#### Rutina de desembarque

In [862]:
def rutina_desembarque(t_suc): 
    # avion en aeropuerto: desembarcan pasajeros, embarcan los nuevos y traslado a pistas
    global t, n1, n2, n3, NLL1, LL1, LISTA, LANDING, S3, DEPARTURE, acumulo_pistas_ocupadas, cambio_pistas_ocupadas
    global n_med_n1, n_med_n2, n_med_n3
    global esperando_a_despegar, esperando_a_aterrizar, esperando_coche, esperando_puerta
    
    n_med_n1 += n1 * (t_suc - t) #tiempo trascurrido hasta el suceso * nº aviones
    n_med_n2 += n2 * (t_suc - t)
    n_med_n3 += n3 * (t_suc - t)
    
    t=t_suc     # Actualizamos tº de simulación
    
    n2 -=1      # El avión sale de n2 y libera su vehículo.
    
    #si hay puertas de embarque disponibles
    if n3 < nPuertas:

        n3 +=1      # El avión entra en n3, y ocupa una puerta
        
        Z = t_desembarques()
        LISTA['tS3'][LISTA['tS3'].index(10E9)] = t + Z

        if events: print(f'--PUERTA ASIGNADA: {n3} puertas ocupadas. Minuto: {t}. Fin de proceso: {t+Z}')
        
    else: # si no hay puertas disponibles 
        esperando_puerta+=1     # esperando puerta embarque
        if events: print(f'--ESPERANDO PUERTA: {esperando_puerta} aviones esperando. Minuto: {t}')

    # si tengo aviones pendientes de ser trasladados
    if esperando_coche > 0: 

        n2+=1                       # El avión en cola entra al n2, ocupa un coche,
        esperando_coche -= 1        # Y libera su puesto en la cola.
        
        Y = t_traslado()
        LISTA['tS2'][LISTA['tS2'].index(10E9)] = t + Y

        if events: print(f'-TRASLADO_cola: {n2} coches ocupados. Minuto {t}. Fin de traslado {t+Z}')

#### Rutina de despegue (vuelta al nodo 1)

In [863]:
def rutina_despegue(t_suc): 
    # sale del nodo 3 y espera a poder salir del sistema (nodo SS)    
    global t, n1, n2, n3, NLL1, LL1, LISTA, LANDING, S3, DEPARTURE, acumulo_pistas_ocupadas, cambio_pistas_ocupadas
    global n_med_n1, n_med_n2, n_med_n3
    global esperando_a_despegar, esperando_a_aterrizar, esperando_coche, esperando_puerta
    
    n_med_n1 += n1 * (t_suc - t) #tiempo trascurrido hasta el suceso * nº aviones
    n_med_n2 += n2 * (t_suc - t)
    n_med_n3 += n3 * (t_suc - t)
    
    
    t=t_suc     # Actualizamos tº de simulación

    n3 -=1      # El avión sale del n3 y libera un puerta.
    
    S3.append(t)
    
    # Si hay pistas libres
    if n1 < nPistas:
        
        n1+=1               # El avión entra al n1 y ocupa una pista
        
        if cambio_pistas_ocupadas > 0:
            acumulo_pistas_ocupadas += t_suc - cambio_pistas_ocupadas
            if tiempos: print(f'PISTA LIBRE AT {t_suc}. Acumulo {t_suc - cambio_pistas_ocupadas} -> {acumulo_pistas_ocupadas}')
            cambio_pistas_ocupadas = 0

        # generamos tiempo de despegue
        Z = t_salidas()
        LISTA['tSS'][LISTA['tSS'].index(10E9)] = t + Z
        DEPARTURE.append(t)
        if events: print(f'---DESPEGUE: {n1} pistas ocupadas. Minuto: {t}. Fin de maniobra: {t+Z}')

    else:    
        esperando_a_despegar+=1 #esperando para el despegue
        #si ya estaban ocupadas de antes, no actualices y quédate con el primero
        if cambio_pistas_ocupadas > 0 and t_suc > 0: 
            cambio_pistas_ocupadas = min(t_suc, cambio_pistas_ocupadas)
            if tiempos: print(f'Pista ocupada despegue en (t_suc, cambio) {t_suc, cambio_pistas_ocupadas} pero lo estaba antes en {cambio_pistas_ocupadas}')
        #si no lo estaban, actualiza el tiempo
        cambio_pistas_ocupadas = t_suc
        if tiempos: print(f'NO HAY PISTAS LIBRES at {cambio_pistas_ocupadas}')
        if events: print(f'---ESPERANDO DESPEGAR: {esperando_a_despegar} aviones esperando. Minuto: {t}')

    # Manejo la cola del nodo anterior
    # si quedan aviones esperando puerta
    if esperando_puerta > 0:
        
        n3+=1                   # El avion entra al n3, ocupa una puerta
        esperando_puerta-=1     # Y libera su puesto en la cola

        Y = t_desembarques()    # Genero tiempo de desembarque
        LISTA['tS3'][LISTA['tS3'].index(10E9)] = t + Y

        if events: print(f'--PUERTA ASIGNADA_cola: {n3} puertas ocupadas. Minuto: {t}. Fin de proceso: {t+Z}')

#### Rutina de salida

In [864]:
def rutina_salida_sistema(t_suc): 
    # sale del nodo 3 y espera a poder salir del sistema (nodo SS)    
    global t, n1, n2, n3, NLL1, LL1, LISTA, LANDING, S3, DEPARTURE, acumulo_pistas_ocupadas, cambio_pistas_ocupadas
    global n_med_n1, n_med_n2, n_med_n3
    global esperando_a_despegar, esperando_a_aterrizar, esperando_coche, esperando_puerta
    
    n_med_n1 += n1 * (t_suc - t) #tiempo trascurrido hasta el suceso * nº aviones
    n_med_n2 += n2 * (t_suc - t)
    n_med_n3 += n3 * (t_suc - t)
    
    t=t_suc     # Actualizamos tº de simulación

    n1 -=1      # El avión sale del nodo 1 y despeja una pista.
    if events: print(f'----SALIDA DE SISTEMA: {n1} pistas ocupadas. Minuto: {t}.')

    if events: print(f'---------------------: Esperando aterrizar: {esperando_a_aterrizar}, Esperando despegar: {esperando_a_despegar}')

    # Manejo la cola del nodo anterior  
    if esperando_a_aterrizar > 0: # ahora que se han liberado pistas, atendemos a la cola de aterrizaje
        Z = t_aterrizaje()                              # genero tiempo que tardará en aterrizar
        LISTA['tS1'][LISTA['tS1'].index(10E9)] = t + Z  # registro el tiempo en el que saldrá el avión del nodo 1
        LANDING.append(t)
        n1+=1                       # El avión en cola entra al n1, ocupa una pista,
        esperando_a_aterrizar -= 1  # y libera su puesto en la cola.

        if events: print(f'ATERRIZAJE_cola: {n1} pistas ocupadas. Minuto: {t}. Fin de maniobra: {t+Z}')
        
    elif esperando_a_despegar > 0:

        if esperando_a_aterrizar>0: return -1
        
        n1+=1                       # El avión en cola entra al n1, ocupa una pista,
        esperando_a_despegar -=1    # Y libera su puesto en la cola.
        
        DEPARTURE.append(t)
        
        Z = t_salidas()                                 # genero tiempo que tardará en despegar
        LISTA['tSS'][LISTA['tSS'].index(10E9)] = t + Z  # registro el tiempo en el que saldrá el avión del nodo 1

        
        if events: print(f'---DESPEGUE_cola: {n1} pistas ocupadas. Minuto: {t}. Fin de maniobra: {t+Z}')


# MAIN

In [865]:

def simul_main():
    global LISTA

    reiniciar_variables()
    
    # Genero primer evento (aterrizaje)
    X = t_llegada(0)
    
    # Caso especial
    if X > T:
        return
    
    rutina_aterrizaje(X)

    # Bucle principal
    # While haya eventos pendientes (tiempos en la lista)
    while any(min(val) != 10E9 if isinstance(val, list) else val != 10E9 for val in LISTA.values()):
        min_key = min(
            LISTA.keys(), 
            key=lambda k: min(LISTA[k]) if isinstance(LISTA[k], list) else LISTA[k]
        )
        if verbose: print(LISTA)
        if verbose: print(min_key, LISTA[min_key])
        if verbose: print ()

        if(min_key=='tLL1'): # Si el próximo evento es un aterrizaje (LLN1)
            t_suc=LISTA['tLL1']
            LISTA['tLL1']= 10E9
            rutina_aterrizaje(t_suc)
            
        elif(min_key=='tS1'): # Si el próximo evento es un traslado (SN1)
            t_suc=min(LISTA['tS1'])
            LISTA['tS1'][LISTA['tS1'].index(min(LISTA['tS1']))] = 10E9
            rutina_traslado(t_suc)
            
        elif(min_key=='tS2'): # Si el próximo evento es un desembarque (SN2)
            t_suc=min(LISTA['tS2'])
            LISTA['tS2'][LISTA['tS2'].index(min(LISTA['tS2']))] = 10E9
            rutina_desembarque(t_suc)
            
        elif(min_key=='tS3'): # Si el próximo evento es una preparación para despegue (SN3)
            t_suc=min(LISTA['tS3'])
            LISTA['tS3'][LISTA['tS3'].index(min(LISTA['tS3']))] = 10E9
            rutina_despegue(t_suc)
            
        elif(min_key=='tSS'): # Si el próximo evento es una salida de sistema (SN4)
            t_suc=min(LISTA['tSS'])
            LISTA['tSS'][LISTA['tSS'].index(min(LISTA['tSS']))] = 10E9
            rutina_salida_sistema(t_suc)    

In [866]:
simul_main()
Tp = max(0,t-T)
print('----El horizonte temporal de la simulación eran '+ str(round(T/60,2)) + 'h ~ '+str(T)+' minutos.----')
print('----La simulación ha terminado completamente en el minuto '+ str(T + Tp) + ' ~ '+str(round(T + Tp/60,2))+'h.----')

ATERRIZAJE: 1 pistas ocupadas. Minuto: 16.24543035365374. Fin de maniobra: 23.932672428252726
-TRASLADO: 1 coches ocupados. Minuto 23.932672428252726. Fin de traslado 24.63905953322453
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 24.63905953322453. Fin de proceso: 24.67123969613908
---DESPEGUE: 1 pistas ocupadas. Minuto: 24.67123969613908. Fin de maniobra: 35.18106057906081
ATERRIZAJE: 2 pistas ocupadas. Minuto: 32.28714003224938. Fin de maniobra: 42.933365833560956
----SALIDA DE SISTEMA: 1 pistas ocupadas. Minuto: 35.18106057906081.
---------------------: Esperando aterrizar: 0, Esperando despegar: 0
-TRASLADO: 1 coches ocupados. Minuto 42.933365833560956. Fin de traslado 44.01598231640829
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 44.01598231640829. Fin de proceso: 44.18576082136395
---DESPEGUE: 1 pistas ocupadas. Minuto: 44.18576082136395. Fin de maniobra: 56.60162169535885
ATERRIZAJE: 2 pistas ocupadas. Minuto: 56.0280633532942. Fin de maniobra: 64.26992371590168
----SALIDA D


----SALIDA DE SISTEMA: 2 pistas ocupadas. Minuto: 4687.519630810081.
---------------------: Esperando aterrizar: 0, Esperando despegar: 87
---DESPEGUE_cola: 3 pistas ocupadas. Minuto: 4687.519630810081. Fin de maniobra: 4698.594517158912
----SALIDA DE SISTEMA: 2 pistas ocupadas. Minuto: 4687.682937935488.
---------------------: Esperando aterrizar: 0, Esperando despegar: 86
---DESPEGUE_cola: 3 pistas ocupadas. Minuto: 4687.682937935488. Fin de maniobra: 4698.253403913535
ESPERANDO ATERRIZAR: 1 aviones esperando. Minuto 4687.682937935488
ESPERANDO ATERRIZAR: 2 aviones esperando. Minuto 4687.682937935488
----SALIDA DE SISTEMA: 2 pistas ocupadas. Minuto: 4698.253403913535.
---------------------: Esperando aterrizar: 2, Esperando despegar: 85
ATERRIZAJE_cola: 3 pistas ocupadas. Minuto: 4698.253403913535. Fin de maniobra: 4704.177531820825
----SALIDA DE SISTEMA: 2 pistas ocupadas. Minuto: 4698.594517158912.
---------------------: Esperando aterrizar: 1, Esperando despegar: 85
ATERRIZAJE_co

In [867]:
print(n1)
print(n2)
print(n3)
print(n_med_n1/t)
print(n_med_n2/t)
print(n_med_n3/t)
print(f'{(n_med_n1+n_med_n2+n_med_n3)/t}')

0
0
0
3.915424926722788
0.06985655241484064
0.01362909492020807
3.998910574057837


In [868]:
t_espera_aterrizaje = [a - b for a, b in zip(LANDING, LL1)]
print(f'{len(t_espera_aterrizaje)} aviones han aterrizado')
print(f'El tiempo máximo de espera de aterrizaje ha sido de {round(max(t_espera_aterrizaje),2)} minutos ~ {round(max(t_espera_aterrizaje)/60,2)}h.')
print(f'El tiempo medio de espera de aterrizaje ha sido de {round(sum(t_espera_aterrizaje)/len(t_espera_aterrizaje),2)} minutos ~ {round(sum(t_espera_aterrizaje)/len(t_espera_aterrizaje)/60,2)}h.')
print()
t_espera_despegue = [a - b for a, b in zip(DEPARTURE, S3)]
print(f'{len(t_espera_despegue)} aviones han despegado')
print(f'El tiempo máximo de espera de despegue ha sido de {round(max(t_espera_despegue),2)} minutos ~ {round(max(t_espera_despegue)/60,2)}h.')
print(f'El tiempo medio de espera de despegue ha sido de {round(sum(t_espera_despegue)/len(t_espera_despegue),2)} minutos ~ {round(sum(t_espera_despegue)/len(t_espera_despegue)/60,2)}h.')
print()
print(f'Las pistas han estado ocupadas durante {round(acumulo_pistas_ocupadas, 2)} minutos ~ {round(acumulo_pistas_ocupadas/60,2)}h.')
print(f'Esto es un porcentaje de tiempo del {round(acumulo_pistas_ocupadas*100/t,2)}%.')

6268 aviones han aterrizado
El tiempo máximo de espera de aterrizaje ha sido de 96.15 minutos ~ 1.6h.
El tiempo medio de espera de aterrizaje ha sido de 9.65 minutos ~ 0.16h.

6268 aviones han despegado
El tiempo máximo de espera de despegue ha sido de 7130.06 minutos ~ 118.83h.
El tiempo medio de espera de despegue ha sido de 3546.47 minutos ~ 59.11h.

Las pistas han estado ocupadas durante 22039.28 minutos ~ 367.32h.
Esto es un porcentaje de tiempo del 46.51%.


# TESTS

In [869]:
T=30*24*60
nCoches = nCoches + 5
nPistas = nPistas + 1
simul_main()
Tp = max(0,t-T)
print('----El horizonte temporal de la simulación eran '+ str(round(T/60,2)) + 'h ~ '+str(T)+' minutos.----')
print('----La simulación ha terminado completamente en el minuto '+ str(T + Tp) + ' ~ '+str(round(T + Tp/60,2))+'h.----')

ATERRIZAJE: 1 pistas ocupadas. Minuto: 6.533547031288263. Fin de maniobra: 21.392877618768445
ATERRIZAJE: 2 pistas ocupadas. Minuto: 8.865496123597767. Fin de maniobra: 21.80905709770969
ATERRIZAJE: 3 pistas ocupadas. Minuto: 18.831031389856946. Fin de maniobra: 23.942648486062744
-TRASLADO: 1 coches ocupados. Minuto 21.392877618768445. Fin de traslado 21.80463746457391
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 21.80463746457391. Fin de proceso: 21.853631250184502
-TRASLADO: 1 coches ocupados. Minuto 21.80905709770969. Fin de traslado 22.339190268616658
---DESPEGUE: 2 pistas ocupadas. Minuto: 21.853631250184502. Fin de maniobra: 36.47665927970321
ATERRIZAJE: 3 pistas ocupadas. Minuto: 21.958280695203875. Fin de maniobra: 31.570916836418185
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 22.339190268616658. Fin de proceso: 22.62073165421169
---DESPEGUE: 4 pistas ocupadas. Minuto: 22.62073165421169. Fin de maniobra: 33.00983423336206
-TRASLADO: 1 coches ocupados. Minuto 23.9426484860

In [870]:
print(n1)
print(n2)
print(n3)
print(n_med_n1/t)
print(n_med_n2/t)
print(n_med_n3/t)
print(f'{(n_med_n1+n_med_n2+n_med_n3)/t}')

0
0
0
3.585082316336644
0.06719991495306966
0.012968748917030173
3.665250980206744


In [871]:
print(f'Simulación con {nCoches} vehículos y {nPistas} pistas')
print()
t_espera_aterrizaje = [a - b for a, b in zip(LANDING, LL1)]
print(f'{len(t_espera_aterrizaje)} aviones han aterrizado')
print(f'El tiempo máximo de espera de aterrizaje ha sido de {round(max(t_espera_aterrizaje),2)} minutos ~ {round(max(t_espera_aterrizaje)/60,2)}h.')
print(f'El tiempo medio de espera de aterrizaje ha sido de {round(sum(t_espera_aterrizaje)/len(t_espera_aterrizaje),2)} minutos ~ {round(sum(t_espera_aterrizaje)/len(t_espera_aterrizaje)/60,2)}h.')
print()
t_espera_despegue = [a - b for a, b in zip(DEPARTURE, S3)]
print(f'{len(t_espera_despegue)} aviones han despegado')
print(f'El tiempo máximo de espera de despegue ha sido de {round(max(t_espera_despegue),2)} minutos ~ {round(max(t_espera_despegue)/60,2)}h.')
print(f'El tiempo medio de espera de despegue ha sido de {round(sum(t_espera_despegue)/len(t_espera_despegue),2)} minutos ~ {round(sum(t_espera_despegue)/len(t_espera_despegue)/60,2)}h.')
print()
print(f'Las pistas han estado ocupadas durante {round(acumulo_pistas_ocupadas, 2)} minutos ~ {round(acumulo_pistas_ocupadas/60,2)}h.')
print(f'Esto es un porcentaje de tiempo del {round(acumulo_pistas_ocupadas*100/t,2)}%.')

Simulación con 25 vehículos y 4 pistas

5614 aviones han aterrizado
El tiempo máximo de espera de aterrizaje ha sido de 44.2 minutos ~ 0.74h.
El tiempo medio de espera de aterrizaje ha sido de 3.7 minutos ~ 0.06h.

5614 aviones han despegado
El tiempo máximo de espera de despegue ha sido de 267.91 minutos ~ 4.47h.
El tiempo medio de espera de despegue ha sido de 40.39 minutos ~ 0.67h.

Las pistas han estado ocupadas durante 12572.04 minutos ~ 209.53h.
Esto es un porcentaje de tiempo del 29.1%.
